In [17]:
import numpy as np
import matplotlib.pyplot as plt
import ipywidgets as widgets
from IPython.display import display, clear_output
from collections import defaultdict
from scipy.stats import binom

np.random.seed(42)

%matplotlib inline
%config InlineBackend.figure_format = 'retina'

## Can you generate a random sequence?

Press L or R repeatedly. Try to be unpredictable.

The algorithm predicts your next choice based on patterns in your history. It uses a simple Markov model: given your last few choices, what did you tend to choose next?

In [ ]:
class MarkovPredictor:
    """
    Markov predictor that exploits patterns in sequential choices.
    
    Enhancements over basic Markov:
    1. Higher order (up to 5) for longer pattern detection
    2. Anti-alternation bias (humans alternate too much)
    3. Global frequency bias (humans favor one side)
    """
    
    def __init__(self, max_order=5):
        self.max_order = max_order
        self.history = []
        self.predictions = []
        self.correct = 0
        self.total = 0
        self.counts = {k: defaultdict(lambda: {'L': 0, 'R': 0}) 
                       for k in range(1, max_order + 1)}
        self.global_counts = {'L': 0, 'R': 0}
    
    def predict(self):
        if len(self.history) < 1:
            return 'L', 0.5
        
        # Try Markov prediction from highest to lowest order
        for order in range(min(self.max_order, len(self.history)), 0, -1):
            context = tuple(self.history[-order:])
            counts = self.counts[order][context]
            total = counts['L'] + counts['R']
            
            if total >= 1:  # Lower threshold for faster learning
                if counts['L'] > counts['R']:
                    return 'L', counts['L'] / total
                elif counts['R'] > counts['L']:
                    return 'R', counts['R'] / total
        
        # Fallback 1: Exploit global bias if strong
        total_global = self.global_counts['L'] + self.global_counts['R']
        if total_global >= 5:
            l_rate = self.global_counts['L'] / total_global
            if l_rate > 0.6:
                return 'L', l_rate
            elif l_rate < 0.4:
                return 'R', 1 - l_rate
        
        # Fallback 2: Anti-alternation (humans alternate too much)
        last = self.history[-1]
        return ('R' if last == 'L' else 'L'), 0.55
    
    def update(self, choice):
        # Update all Markov orders
        for order in range(1, min(self.max_order, len(self.history)) + 1):
            context = tuple(self.history[-order:])
            self.counts[order][context][choice] += 1
        
        # Update global counts
        self.global_counts[choice] += 1
        
        self.history.append(choice)
    
    def record_prediction(self, prediction, actual):
        self.predictions.append((prediction, actual))
        self.total += 1
        if prediction == actual:
            self.correct += 1
    
    @property
    def accuracy(self):
        return self.correct / self.total if self.total > 0 else 0.0

In [ ]:
# Visual interface
predictor = MarkovPredictor(max_order=5)
current_prediction = [None, None]

# Single output area (avoids duplication issues)
main_output = widgets.Output()

def render_display():
    """Render all UI elements as a single HTML block."""
    if predictor.total == 0:
        return "<p style='font-size: 16px; color: #666;'>Press L or R to begin...</p>"
    
    acc = predictor.accuracy * 100
    edge = (predictor.accuracy - 0.5) * 100
    edge_color = '#4CAF50' if edge > 0 else '#f44336' if edge < 0 else '#666'
    
    # History boxes
    boxes_html = ""
    if len(predictor.predictions) > 0:
        recent = predictor.predictions[-20:]
        boxes = []
        for pred, actual in recent:
            correct = pred == actual
            color = '#4CAF50' if correct else '#f44336'
            boxes.append(
                f'<div style="display:inline-block; width:28px; height:28px; '
                f'background-color:{color}; color:white; text-align:center; '
                f'line-height:28px; margin:2px; border-radius:4px; font-size:14px;">'
                f'{actual}</div>'
            )
        boxes_html = f'''
        <div style="margin-top: 15px;">
            <div style="font-size: 12px; color: #666; margin-bottom: 5px;">Recent trials (green = predicted correctly):</div>
            {''.join(boxes)}
        </div>
        '''
    
    html = f'''
    <div style="font-family: -apple-system, BlinkMacSystemFont, 'Segoe UI', Roboto, sans-serif;">
        <div style="margin: 10px 0;">
            <div style="display: flex; align-items: center; margin-bottom: 5px;">
                <span style="width: 80px; font-weight: bold;">Accuracy:</span>
                <span style="font-size: 18px; font-weight: bold;">{acc:.1f}%</span>
                <span style="margin-left: 10px; color: #666;">({predictor.correct}/{predictor.total})</span>
            </div>
            <div style="position: relative; width: 100%; height: 30px; background-color: #e0e0e0; border-radius: 4px;">
                <div style="position: absolute; left: 50%; top: 0; bottom: 0; width: 2px; background-color: #333; z-index: 2;"></div>
                <div style="position: absolute; left: 50%; top: -18px; transform: translateX(-50%); font-size: 11px; color: #666;">chance</div>
                <div style="position: absolute; left: 0; top: 0; bottom: 0; width: {acc}%; 
                            background-color: {'#4CAF50' if acc >= 50 else '#f44336'}; 
                            border-radius: 4px; transition: width 0.3s;"></div>
                <div style="position: absolute; left: 5px; top: 50%; transform: translateY(-50%); color: white; font-weight: bold; font-size: 12px;">0%</div>
                <div style="position: absolute; right: 5px; top: 50%; transform: translateY(-50%); color: #666; font-size: 12px;">100%</div>
            </div>
        </div>
        <div style="margin-top: 15px;">
            <span style="font-size: 14px;">Edge over chance: </span>
            <span style="font-size: 16px; font-weight: bold; color: {edge_color};">{edge:+.1f}%</span>
        </div>
        {boxes_html}
    </div>
    '''
    return html

def display_ui():
    """Update display - clears and rewrites entire output."""
    main_output.clear_output(wait=True)
    with main_output:
        display(widgets.HTML(render_display()))

def on_click(choice):
    pred, conf = current_prediction
    predictor.record_prediction(pred, choice)
    predictor.update(choice)
    next_pred, next_conf = predictor.predict()
    current_prediction[0] = next_pred
    current_prediction[1] = next_conf
    display_ui()

# Create buttons
btn_L = widgets.Button(
    description='L', 
    button_style='info',
    layout=widgets.Layout(width='120px', height='60px')
)
btn_R = widgets.Button(
    description='R', 
    button_style='info',
    layout=widgets.Layout(width='120px', height='60px')
)

btn_L.on_click(lambda b: on_click('L'))
btn_R.on_click(lambda b: on_click('R'))

# Initialize prediction
current_prediction[0], current_prediction[1] = predictor.predict()

# Layout - single VBox with single output
title = widgets.HTML(
    '<h3 style="margin-bottom: 5px;">Can you generate a random sequence?</h3>'
    '<p style="color: #666; margin-top: 0;">Press L or R repeatedly. Try to be unpredictable.</p>'
)
buttons = widgets.HBox(
    [btn_L, btn_R], 
    layout=widgets.Layout(justify_content='center', margin='20px 0')
)

ui = widgets.VBox([
    title,
    buttons,
    main_output
], layout=widgets.Layout(padding='20px', max_width='600px'))

display(ui)
display_ui()

### Results

The sequence you generated has probability $(1/2)^n$, identical to any other sequence of length $n$. Yet the algorithm exploited structure you didn't intend to create.

In [ ]:
# Final results
n = predictor.total
acc = predictor.accuracy * 100
edge = (predictor.accuracy - 0.5) * 100

print(f"Final: {predictor.correct}/{n} ({acc:.1f}%)  |  Edge: {edge:+.1f}%")
print(f"Sequence probability: (1/2)^{n} = {0.5**n:.2e}")

# Global bias
l_pct = predictor.global_counts['L'] / n * 100 if n > 0 else 50
print(f"L/R split: {l_pct:.0f}% / {100-l_pct:.0f}%")

# Pattern heatmap
fig, ax = plt.subplots(figsize=(5, 3.5))

contexts = [('L','L'), ('L','R'), ('R','L'), ('R','R')]
data = []
annotations = []

for ctx in contexts:
    counts = predictor.counts[2][ctx]
    total = counts['L'] + counts['R']
    if total > 0:
        l_prob = counts['L'] / total
        data.append([l_prob, 1 - l_prob])
        annotations.append([f"{counts['L']}", f"{counts['R']}"])
    else:
        data.append([0.5, 0.5])
        annotations.append(["-", "-"])

data = np.array(data)
im = ax.imshow(data, cmap='RdYlGn', aspect='auto', vmin=0, vmax=1)

ax.set_xticks([0, 1])
ax.set_xticklabels(['-> L', '-> R'], fontsize=11)
ax.set_yticks(range(4))
ax.set_yticklabels(['LL', 'LR', 'RL', 'RR'], fontsize=11)

for i in range(4):
    for j in range(2):
        ax.text(j, i, annotations[i][j], ha='center', va='center', 
                fontsize=11, color='black' if 0.3 < data[i,j] < 0.7 else 'white')

ax.set_title('What you chose after each context', fontsize=11)
plt.colorbar(im, ax=ax, shrink=0.8)
plt.tight_layout()
plt.show()

## Small samples

How many coin flips to determine if a coin is fair? Run the cell below multiple times.

In [ ]:
n_flips = 10
n_repeats = 20
threshold = 7

count = 0
for _ in range(n_repeats):
    result = np.random.binomial(n_flips, 0.5)
    mark = " \u2713" if result >= threshold else ""
    if result >= threshold:
        count += 1
    print(f"{n_flips} flips: {result} heads ({result/n_flips*100:.0f}%){mark}")

print(f"\nSummary: {count}/{n_repeats} had {threshold}+ heads ({count/n_repeats*100:.0f}%)")

With $n=10$ flips, observing 7 or more heads happens about 17% of the time even with a fair coin.

In [ ]:
n_flips = 10
# adjust: 100, 1000, 10000
n_experiments = 100

results = np.random.binomial(n_flips, 0.5, n_experiments)

fig, ax = plt.subplots(figsize=(10, 5))

ax.hist(results, bins=np.arange(-0.5, n_flips+1.5, 1), 
        density=True, alpha=0.7, color='steelblue', edgecolor='white', label='Observed')

x = np.arange(0, n_flips+1)
pmf = binom.pmf(x, n_flips, 0.5)
ax.plot(x, pmf, 'ro-', markersize=8, linewidth=2, label='Binomial(10, 0.5)')

p_extreme = binom.sf(6, n_flips, 0.5)
ax.axvline(x=7, color='red', linestyle='--', alpha=0.5)
ax.text(7.5, ax.get_ylim()[1]*0.8, f'P(X >= 7) = {p_extreme:.1%}', fontsize=11)

ax.set_xlabel('Number of heads', fontsize=12)
ax.set_ylabel('Probability', fontsize=12)
ax.legend(fontsize=11)
ax.set_xticks(range(0, n_flips+1))
plt.tight_layout()
plt.show()

### Sample size effect

The distribution of sample proportions narrows as $1/\sqrt{n}$. To halve uncertainty, quadruple sample size.

In [ ]:
fig, axes = plt.subplots(1, 4, figsize=(14, 3.5))
sample_sizes = [10, 50, 100, 500]
n_experiments = 10000

for ax, n in zip(axes, sample_sizes):
    results = np.random.binomial(n, 0.5, n_experiments)
    proportions = results / n
    
    ax.hist(proportions, bins=30, density=True, alpha=0.7, 
            color='steelblue', edgecolor='white')
    
    lower = binom.ppf(0.025, n, 0.5) / n
    upper = binom.ppf(0.975, n, 0.5) / n
    ax.axvline(lower, color='red', linestyle='--', linewidth=1.5)
    ax.axvline(upper, color='red', linestyle='--', linewidth=1.5)
    
    width = upper - lower
    ax.set_title(f'n = {n}\n95% interval width: {width:.2f}', fontsize=11)
    ax.set_xlabel('Proportion heads', fontsize=10)
    ax.set_xlim(0.2, 0.8)

axes[0].set_ylabel('Density', fontsize=10)
plt.tight_layout()
plt.show()

## Statistical regularity

Individual outcomes are unpredictable. Aggregate behavior is highly structured.

The following is a *prediction* from the binomial distribution—not a fit to data.

In [ ]:
n_flips = 100
n_students = 10000

x = np.arange(0, n_flips + 1)
pmf = binom.pmf(x, n_flips, 0.5)

fig, ax = plt.subplots(figsize=(10, 5))
ax.plot(x, pmf, 'b-', linewidth=2)
ax.fill_between(x, pmf, alpha=0.3)
ax.set_xlabel('Number of heads', fontsize=12)
ax.set_ylabel('Probability', fontsize=12)
ax.set_title(f'Theoretical prediction: {n_students:,} students, {n_flips} flips each', fontsize=12)
ax.set_xlim(30, 70)
plt.tight_layout()
plt.show()

### Convergence

Each trajectory is different. Each trajectory converges to $p = 0.5$.

In [ ]:
n_trajectories = 20
n_flips = 1000

fig, ax = plt.subplots(figsize=(10, 5))

for i in range(n_trajectories):
    flips = np.random.binomial(1, 0.5, n_flips)
    running_avg = np.cumsum(flips) / np.arange(1, n_flips + 1)
    ax.plot(running_avg, alpha=0.5, linewidth=0.8)

ax.axhline(y=0.5, color='red', linestyle='--', linewidth=2, label='p = 0.5')
ax.set_xlabel('Number of flips', fontsize=12)
ax.set_ylabel('Running proportion of heads', fontsize=12)
ax.set_ylim(0.2, 0.8)
ax.set_xlim(0, n_flips)
ax.legend(fontsize=11)
plt.tight_layout()
plt.show()

### Verification

Compare the theoretical prediction to simulated data.

In [ ]:
n_flips = 100
n_students = 10000

results = np.random.binomial(n_flips, 0.5, n_students)

x = np.arange(0, n_flips + 1)
pmf = binom.pmf(x, n_flips, 0.5)

fig, ax = plt.subplots(figsize=(10, 5))

ax.hist(results, bins=np.arange(29.5, 71.5, 1), density=True, 
        alpha=0.7, color='steelblue', edgecolor='white', label='Simulated')
ax.plot(x, pmf, 'r-', linewidth=2.5, label='Prediction')

ax.set_xlabel('Number of heads', fontsize=12)
ax.set_ylabel('Probability', fontsize=12)
ax.set_xlim(30, 70)
ax.legend(fontsize=11)
plt.tight_layout()
plt.show()